# <center style="font-family: consolas; font-size: 32px; font-weight: bold;"> Google - 🤟American Sign Language Fingerspelling Recognition🖖</center>
<p><center style="color:#949494; font-family: consolas; font-size: 20px;">Train fast and accurate American Sign Language fingerspelling recognition models</center></p>

***

# <center style="font-family: consolas; font-size: 32px; font-weight: bold;">(ಠಿ⁠_⁠ಠ) Overview</center>

<p style="font-family: consolas; font-size: 16px;">⚪ The goal of the competition is to detect and translate American Sign Language (ASL) fingerspelling into text.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ The competition is based on a large dataset of over three million fingerspelled characters produced by over 100 Deaf signers captured via the selfie camera of a smartphone with a variety of backgrounds and lighting conditions.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ The competition aims to improve sign language recognition technology, making it more accessible for the Deaf and Hard of Hearing community.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ Fingerspelling is an important part of ASL and is often used for communicating names, addresses, phone numbers, and other information commonly entered on a mobile phone.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ ASL fingerspelling can be substantially faster than typing on a smartphone’s virtual keyboard.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ Sign language recognition AI for text entry lags far behind voice-to-text or even gesture-based typing, as robust datasets didn't previously exist.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ Participating in this competition could help provide Deaf and Hard of Hearing users with the option to fingerspell words instead of using a keyboard, enabling them to communicate with hearing non-signers more quickly and smoothly.</p>

#### <a id="top"></a>
# <div style="box-shadow: rgb(60, 121, 245) 0px 0px 0px 3px inset, rgb(255, 255, 255) 10px -10px 0px -3px, rgb(31, 193, 27) 10px -10px, rgb(255, 255, 255) 20px -20px 0px -3px, rgb(255, 217, 19) 20px -20px, rgb(255, 255, 255) 30px -30px 0px -3px, rgb(255, 156, 85) 30px -30px, rgb(255, 255, 255) 40px -40px 0px -3px, rgb(255, 85, 85) 40px -40px; padding:20px; margin-right: 40px; font-size:30px; font-family: consolas; text-align:center; display:fill; border-radius:15px; color:rgb(60, 121, 245);"><b>Table of contents</b></div>

<div style="background-color: rgba(60, 121, 245, 0.03); padding:30px; font-size:15px; font-family: consolas;">
<ul>
    <li><a href="#0" target="_self" rel=" noreferrer nofollow">0. Import all dependencies</a></li>
    <li><a href="#1" target="_self" rel=" noreferrer nofollow">1. Data overview</a></li>
    <li><a href="#2" target="_self" rel=" noreferrer nofollow">2. Train overview</a></li>
    <li><a href="#3" target="_self" rel=" noreferrer nofollow">3. Supplemental overview</a></li>
</ul>
</div>

<a id="0"></a>
# <div style="box-shadow: rgba(0, 0, 0, 0.16) 0px 1px 4px inset, rgb(51, 51, 51) 0px 0px 0px 3px inset; padding:20px; font-size:32px; font-family: consolas; text-align:center; display:fill; border-radius:15px;  color:rgb(34, 34, 34);"> <b> 0. Import all dependencies </b></div>

In [1]:
# import the desired packages
import numpy as np
import pandas as pd
import json
import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = "simple_white"

In [2]:
def map_new_to_old_style(sequence):
    types = []
    landmark_indexes = []
    for column in list(sequence.columns)[1:544]:
        parts = column.split("_")
        if len(parts) == 4:
            types.append(parts[1] + "_" + parts[2])
        else:
            types.append(parts[1])

        landmark_indexes.append(int(parts[-1]))

    data = {
        "frame": [],
        "type": [],
        "landmark_index": [],
        "x": [],
        "y": [],
        "z": []
    }

    for index, row in sequence.iterrows():
        data["frame"] += [int(row.frame)]*543
        data["type"] += types
        data["landmark_index"] += landmark_indexes

        for _type, landmark_index in zip(types, landmark_indexes):
            data["x"].append(row[f"x_{_type}_{landmark_index}"])
            data["y"].append(row[f"y_{_type}_{landmark_index}"])
            data["z"].append(row[f"z_{_type}_{landmark_index}"])

    return pd.DataFrame.from_dict(data)

# assign desired colors to landmarks
def assign_color(row):
    if row == 'face':
        return 'red'
    elif 'hand' in row:
        return 'dodgerblue'
    else:
        return 'green'

# specifies the plotting order
def assign_order(row):
    if row.type == 'face':
        return row.landmark_index + 101
    elif row.type == 'pose':
        return row.landmark_index + 30
    elif row.type == 'left_hand':
        return row.landmark_index + 80
    else:
        return row.landmark_index

def visualise2d_landmarks(parquet_df, title=""):
    connections = [  
        [0, 1, 2, 3, 4,],
        [0, 5, 6, 7, 8],
        [0, 9, 10, 11, 12],
        [0, 13, 14, 15, 16],
        [0, 17, 18, 19, 20],

        
        [38, 36, 35, 34, 30, 31, 32, 33, 37],
        [40, 39],
        [52, 46, 50, 48, 46, 44, 42, 41, 43, 45, 47, 49, 45, 51],
        [42, 54, 56, 58, 60, 62, 58],
        [41, 53, 55, 57, 59, 61, 57],
        [54, 53],

        
        [80, 81, 82, 83, 84, ],
        [80, 85, 86, 87, 88],
        [80, 89, 90, 91, 92],
        [80, 93, 94, 95, 96],
        [80, 97, 98, 99, 100], ]

    parquet_df = map_new_to_old_style(parquet_df)
    frames = sorted(set(parquet_df.frame))
    first_frame = min(frames)
    parquet_df['color'] = parquet_df.type.apply(lambda row: assign_color(row))
    parquet_df['plot_order'] = parquet_df.apply(lambda row: assign_order(row), axis=1)
    first_frame_df = parquet_df[parquet_df.frame == first_frame].copy()
    first_frame_df = first_frame_df.sort_values(["plot_order"]).set_index('plot_order')


    frames_l = []
    for frame in frames:
        filtered_df = parquet_df[parquet_df.frame == frame].copy()
        filtered_df = filtered_df.sort_values(["plot_order"]).set_index("plot_order")
        traces = [go.Scatter(
            x=filtered_df['x'],
            y=filtered_df['y'],
            mode='markers',
            marker=dict(
                color=filtered_df.color,
                size=9))]

        for i, seg in enumerate(connections):
            trace = go.Scatter(
                    x=filtered_df.loc[seg]['x'],
                    y=filtered_df.loc[seg]['y'],
                    mode='lines',
            )
            traces.append(trace)
        frame_data = go.Frame(data=traces, traces = [i for i in range(17)])
        frames_l.append(frame_data)

    traces = [go.Scatter(
        x=first_frame_df['x'],
        y=first_frame_df['y'],
        mode='markers',
        marker=dict(
            color=first_frame_df.color,
            size=9
        )
    )]
    for i, seg in enumerate(connections):
        trace = go.Scatter(
            x=first_frame_df.loc[seg]['x'],
            y=first_frame_df.loc[seg]['y'],
            mode='lines',
            line=dict(
                color='black',
                width=2
            )
        )
        traces.append(trace)
    fig = go.Figure(
        data=traces,
        frames=frames_l
    )


    fig.update_layout(
        width=500,
        height=800,
        scene={
            'aspectmode': 'data',
        },
        updatemenus=[
            {
                "buttons": [
                    {
                        "args": [None, {"frame": {"duration": 100,
                                                  "redraw": True},
                                        "fromcurrent": True,
                                        "transition": {"duration": 0}}],
                        "label": "&#9654;",
                        "method": "animate",
                    },

                ],
                "direction": "left",
                "pad": {"r": 100, "t": 100},
                "font": {"size":30},
                "type": "buttons",
                "x": 0.1,
                "y": 0,
            }
        ],
    )
    camera = dict(
        up=dict(x=0, y=-1, z=0),
        eye=dict(x=0, y=0, z=2.5)
    )
    fig.update_layout(title_text=title, title_x=0.5)
    fig.update_layout(scene_camera=camera, showlegend=False)
    fig.update_layout(xaxis = dict(visible=False),
            yaxis = dict(visible=False),
    )
    fig.update_yaxes(autorange="reversed")

    fig.show()


def get_phrase(df, file_id, sequence_id):
    return df[
        np.logical_and(
            df.file_id == file_id, 
            df.sequence_id == sequence_id
        )
    ].phrase.iloc[0]

<a id="1"></a>
# <div style="box-shadow: rgba(0, 0, 0, 0.16) 0px 1px 4px inset, rgb(51, 51, 51) 0px 0px 0px 3px inset; padding:20px; font-size:32px; font-family: consolas; text-align:center; display:fill; border-radius:15px;  color:rgb(34, 34, 34);"> <b> 1. Data overview</b></div>

<p style="font-family: consolas; font-size: 16px;">⚪ The goal of this competition is to detect and translate American Sign Language (ASL) fingerspelling into text.</p> 

<p style="font-family: consolas; font-size: 16px;">⚪ <code><b>[train/supplemental_metadata].csv</b></code></p>

* <p style="font-family: consolas; font-size: 16px;"><code>path</code> - The path to the landmark file.</p>
* <p style="font-family: consolas; font-size: 16px;"><code>file_id</code> - A unique identifier for the data file.</p>
* <p style="font-family: consolas; font-size: 16px;"><code>sequence_id</code> - A unique identifier for the landmark sequence. Each data file may contain many sequences.</p>
* <p style="font-family: consolas; font-size: 16px;"><code>phrase</code> - The labels for the landmark sequence. The train and test datasets contain randomly generated addresses, phone numbers, and urls derived from components of real addresses/phone numbers/urls. Any overlap with real addresses, phone numbers, or urls is purely accidental. The supplemental dataset consists of fingerspelled sentences. Note that some of the urls include adult content. The intent of this competition is to support the Deaf and Hard of Hearing community in engaging with technology on an equal footing with other adults.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ <code><b>[train/supplemental]_landmarks/</b></code> - the landmark data. The landmarks were extracted from raw videos with the <a href="https://github.com/google/mediapipe/blob/master/docs/solutions/holistic.md"><strong>MediaPipe holistic model</strong></a>. Not all of the frames necessarily had visible hands or hands that could be detected by the model.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ The landmark files contain the same data as in the ASL Signs competition (minus the row ID column) but reshaped into a wide format. This allows you to take advantage of the Parquet format to entirely skip loading landmarks that you aren't using.</p>

* <p style="font-family: consolas; font-size: 16px;"><code>sequence_id</code> - A unique identifier for the landmark sequence. Most landmark files contain 1,000 sequences. The sequence ID is used as the dataframe index.</p>
* <p style="font-family: consolas; font-size: 16px;"><code>frame</code> - The frame number within a landmark sequence.</p>
* <p style="font-family: consolas; font-size: 16px;"><code>sequence_id</code> - A unique identifier for the landmark sequence. Each data file may contain many sequences.</p>
* <p style="font-family: consolas; font-size: 16px;"><code>[x/y/z]_[type]_[landmark_index]</code> - There are now 1,629 spatial coordinate columns for the x, y and z coordinates for each of the 543 landmarks. The type of landmark is one of ['face', 'left_hand', 'pose', 'right_hand'].</p>

<a id="1.1"></a>
## <div style="box-shadow: rgba(0, 0, 0, 0.18) 0px 2px 4px inset; padding:20px; font-size:24px; font-family: consolas; text-align:center; display:fill; border-radius:15px; color:rgb(67, 66, 66)"> <b> 1.1 American sign language (ASL)</b></div>

<p style="font-family: consolas; font-size: 16px;">⚪ <b>ASL Basics</b>: American Sign Language (ASL) is a complete, natural language that has the same linguistic properties as spoken languages, with grammar that differs from English.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ <b>Sign Language in Different Countries</b>: There is no universal sign language. Different sign languages are used in different countries or regions. Some countries adopt features of ASL in their sign languages.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Origins of ASL</b>: No person or committee invented ASL. The exact beginnings of ASL are not clear, but some suggest that it arose more than 200 years ago from the intermixing of local sign languages and French Sign Language (LSF, or Langue des Signes Française).</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>ASL Compared to Spoken Language</b>: ASL is a language completely separate and distinct from English. It contains all the fundamental features of language, with its own rules for pronunciation, word formation, and word order. Fingerspelling is part of ASL and is used to spell out English words.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Neurobiology of Language Development</b>: Study of sign language can also help scientists understand the neurobiology of language development. Better understanding of the neurobiology of language could provide a translational foundation for treating injury to the language system, for employing signs or gestures in therapy for children or adults, and for diagnosing language impairment in individuals who are deaf.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Sign Languages Created Among Small Communities</b>: The NIDCD is also funding research on sign languages created among small communities of people with little to no outside influence.</p>

<p style="text-align:center;"><img src="https://d.newsweek.com/en/full/1394686/asl-getty-images.webp?w=1400&f=6685541ca5a5e35b027f9bc9957d27c9" width="90%" height="90%"></p>

<p style="text-align:center; font-family: consolas; font-size: 16px;"><i>ASL finger alphabet</i></p>

<a id="1.2"></a>
## <div style="box-shadow: rgba(0, 0, 0, 0.18) 0px 2px 4px inset; padding:20px; font-size:24px; font-family: consolas; text-align:center; display:fill; border-radius:15px; color:rgb(67, 66, 66)"> <b> 1.2 MediaPipe holistic model</b></div>

<p style="font-family: consolas; font-size: 16px;">⚪ MediaPipe Holistic Solution is a powerful, easy-to-use software tool that can detect and track multiple human body parts and gestures in real-time video streams. It is open-source and can run on a variety of platforms, including mobile devices, making it an ideal solution for our competition.</p>

<p style="font-family: consolas; font-size: 16px;">⚪ <b>Real-time Perception:</b> Real-time, simultaneous perception of human pose, face landmarks, and hand tracking can enable impactful applications like fitness analysis, gesture control, and sign language recognition.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Open-Source Framework:</b> MediaPipe is an open-source framework designed for complex perception pipelines.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>State-of-the-Art Solution:</b> MediaPipe Holistic is a solution that provides a state-of-the-art human pose topology, consisting of optimized pose, face, and hand components that each run in real-time.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Unified Topology:</b> MediaPipe Holistic provides a unified topology for 540+ keypoints and is available on-device for mobile and desktop.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Separate ML Models For Separate Tasks:</b> The pipeline integrates separate models for pose, face, and hand components, treating the different regions using a region-appropriate image resolution.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Significant Model Coordination:</b> MediaPipe Holistic requires coordination between up to 8 models per frame and optimized machine learning models and pre- and post-processing algorithms for performance benefits.</p>
<p style="font-family: consolas; font-size: 16px;">⚪ <b>Performance Benefits:</b> The multi-stage nature of the pipeline provides performance benefits, as models are mostly independent and can be replaced with lighter or heavier versions.</p>


<p style="text-align:center;"><img src="https://mediapipe.dev/images/mobile/holistic_sports_and_gestures_example.gif" width="90%" height="90%"></p>

<p style="text-align:center; font-family: consolas; font-size: 16px;"><i><a href="https://google.github.io/mediapipe/solutions/holistic.html">Example of MediaPipe Holistic</a></i></p>


<p style="text-align:center;"><img src="https://mediapipe.dev/images/mobile/hand_landmarks.png" width="90%" height="90%"></p>

<p style="text-align:center; font-family: consolas; font-size: 16px;"><i><a href="https://www.google.com/url?sa=i&url=https%3A%2F%2Fwww.googblogs.com%2Ftag%2Fmediapipe%2F&psig=AOvVaw10h_IFlBkmFPiHLUrQl-Eu&ust=1677514368952000&source=images&cd=vfe&ved=0CBAQjRxqFwoTCOjdt5LKs_0CFQAAAAAdAAAAABAJ">MediaPipe Landmarks for Hands</a></i></p>

<a id="2"></a>
# <div style="box-shadow: rgba(0, 0, 0, 0.16) 0px 1px 4px inset, rgb(51, 51, 51) 0px 0px 0px 3px inset; padding:20px; font-size:32px; font-family: consolas; text-align:center; display:fill; border-radius:15px;  color:rgb(34, 34, 34);"> <b> 2. Train overview</b></div>

<p style="font-family: consolas; font-size: 16px;">⚪ First load train.csv file.</p>

In [3]:
train_df = pd.read_csv("/kaggle/input/asl-fingerspelling/train.csv")

<p style="font-family: consolas; font-size: 16px;">⚪ Let's look how the data looks like.</p>

In [4]:
train_df.head()

path  file_id  sequence_id  participant_id  \
0  train_landmarks/5414471.parquet  5414471   1816796431             217   
1  train_landmarks/5414471.parquet  5414471   1816825349             107   
2  train_landmarks/5414471.parquet  5414471   1816862427               0   
3  train_landmarks/5414471.parquet  5414471   1816909464               1   
4  train_landmarks/5414471.parquet  5414471   1816967051              63   

                phrase  
0         3 creekhouse  
1      scales/kuhaylah  
2       hentaihubs.com  
3  1383 william lanier  
4    988 franklin lane

<p style="font-family: consolas; font-size: 16px;">⚪ Show a discribe of the dataframe with its basic information.</p>

In [5]:
train_df.describe()

file_id   sequence_id  participant_id
count  6.728700e+04  6.728700e+04    67287.000000
mean   1.094617e+09  1.072692e+09      119.762346
std    6.395185e+08  6.177324e+08       74.333078
min    5.414471e+06  7.109500e+04        0.000000
25%    5.277082e+08  5.376403e+08       63.000000
50%    1.099408e+09  1.074263e+09      113.000000
75%    1.662743e+09  1.605478e+09      178.000000
max    2.118949e+09  2.147465e+09      254.000000

<p style="font-family: consolas; font-size: 16px;">🔴 Let's try to visualize sequence <code>1816796431</code> from the file <code>5414471</code>.</p>

In [6]:
sequence_id = 1816796431
file_id = 5414471

In [7]:
path_to_sign = f"/kaggle/input/asl-fingerspelling/train_landmarks/{file_id}.parquet"
sign = pd.read_parquet(path_to_sign)

<p style="font-family: consolas; font-size: 16px;">⚪ Here is what is inside this parquet file:</p>

In [8]:
sign

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1816796431       0  0.710588  0.699951  0.705657  0.691768  0.699669   
1816796431       1  0.709525  0.697582  0.703713  0.691016  0.697576   
1816796431       2  0.711059  0.700858  0.706272  0.693285  0.700825   
1816796431       3  0.712799  0.702518  0.707840  0.694899  0.702445   
1816796431       4  0.712349  0.705451  0.709918  0.696006  0.705180   
...            ...       ...       ...       ...       ...       ...   
1848182207     296  0.657136  0.635888  0.643259  0.619031  0.633084   
1848182207     297  0.655706  0.635570  0.642730  0.618637  0.632830   
1848182207     298  0.653681  0.636057  0.643054  0.618643  0.633258   
1848182207     299  0.654293  0.635543  0.642558  0.617969  0.632699   
1848182207     300  0.655109  0.634491  0.641743  0.617779  0.631771   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
1816796431   0.701980  0.709724  0.610405  0.712660  ...        -0.245855   
1816796431   0.700467  0.709796  0.616540  0.713729  ...              NaN   
1816796431   0.703319  0.711549  0.615606  0.715143  ...              NaN   
1816796431   0.704794  0.712483  0.625044  0.715677  ...        -0.370770   
1816796431   0.706928  0.712685  0.614356  0.714875  ...              NaN   
...               ...       ...       ...       ...  ...              ...   
1848182207   0.631827  0.630708  0.533120  0.626672  ...        -0.143147   
1848182207   0.631554  0.630344  0.531868  0.626445  ...              NaN   
1848182207   0.631800  0.630059  0.531178  0.625990  ...              NaN   
1848182207   0.631167  0.629263  0.531019  0.625069  ...              NaN   
1848182207   0.630562  0.629580  0.533534  0.626065  ...        -0.196495   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
1816796431         -0.269148        -0.129743        -0.251501   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.408097        -0.185217        -0.325494   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1848182207         -0.139659        -0.066276        -0.130910   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207         -0.202258        -0.101019        -0.179127   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
1816796431         -0.278687        -0.266530        -0.152852   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.343373        -0.328294        -0.203126   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1848182207         -0.127341        -0.106674        -0.083439   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207         -0.182757        -0.169923        -0.116275   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
1816796431         -0.257519        -0.275822        -0.266876  
1816796431               NaN              NaN              NaN  
1816796431               NaN              NaN              NaN  
1816796431         -0.315719   

<p style="font-family: consolas; font-size: 16px;">⚪ The number of unique sequences in an <code>.parquet</code> file is <b>1000</b>.</p>

In [9]:
len(np.unique(sign.index))

1000

<p style="font-family: consolas; font-size: 16px;">⚪ Let's get only sequence <code>1816796431</code> from the file.</p>

In [10]:
sequence = sign[sign.index == sequence_id]
sequence

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1816796431       0  0.710588  0.699951  0.705657  0.691768  0.699669   
1816796431       1  0.709525  0.697582  0.703713  0.691016  0.697576   
1816796431       2  0.711059  0.700858  0.706272  0.693285  0.700825   
1816796431       3  0.712799  0.702518  0.707840  0.694899  0.702445   
1816796431       4  0.712349  0.705451  0.709918  0.696006  0.705180   
...            ...       ...       ...       ...       ...       ...   
1816796431     118  0.700922  0.689774  0.695984  0.679756  0.688836   
1816796431     119  0.700576  0.692017  0.697875  0.682405  0.691249   
1816796431     120  0.700621  0.690338  0.696792  0.680982  0.689429   
1816796431     121  0.698651  0.693153  0.699358  0.683020  0.692136   
1816796431     122  0.698450  0.691408  0.697766  0.681728  0.690405   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
1816796431   0.701980  0.709724  0.610405  0.712660  ...        -0.245855   
1816796431   0.700467  0.709796  0.616540  0.713729  ...              NaN   
1816796431   0.703319  0.711549  0.615606  0.715143  ...              NaN   
1816796431   0.704794  0.712483  0.625044  0.715677  ...        -0.370770   
1816796431   0.706928  0.712685  0.614356  0.714875  ...              NaN   
...               ...       ...       ...       ...  ...              ...   
1816796431   0.690414  0.696533  0.596424  0.697664  ...              NaN   
1816796431   0.692938  0.699178  0.598221  0.700476  ...              NaN   
1816796431   0.691177  0.697816  0.599110  0.699297  ...              NaN   
1816796431   0.693553  0.699259  0.599576  0.700144  ...              NaN   
1816796431   0.691932  0.697955  0.601320  0.698955  ...        -0.562035   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
1816796431         -0.269148        -0.129743        -0.251501   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.408097        -0.185217        -0.325494   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.660525        -0.267866        -0.402139   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
1816796431         -0.278687        -0.266530        -0.152852   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.343373        -0.328294        -0.203126   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.499361        -0.567256        -0.253603   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
1816796431         -0.257519        -0.275822        -0.266876  
1816796431               NaN              NaN              NaN  
1816796431               NaN              NaN              NaN  
1816796431         -0.315719   

<p style="font-family: consolas; font-size: 16px;">🔴 Now we can visualize the sequence and the phrase.</p>

In [11]:
sequence_phrase = get_phrase(train_df, file_id, sequence_id)
visualise2d_landmarks(sequence, f"Phrase: {sequence_phrase}")

In [ ]:
#TODO: Plot NaN distributions for some features

In [ ]:
#TODO: Text length distribution

In [ ]:
#TODO: Text lenght distribution

In [ ]:
#TODO: Create participant_id distribution

In [ ]:
#TODO: Frames distribution

<a id="3"></a>
# <div style="box-shadow: rgba(0, 0, 0, 0.16) 0px 1px 4px inset, rgb(51, 51, 51) 0px 0px 0px 3px inset; padding:20px; font-size:32px; font-family: consolas; text-align:center; display:fill; border-radius:15px;  color:rgb(34, 34, 34);"> <b>3. Supplemental overview</b></div>

<p style="font-family: consolas; font-size: 16px;">⚪ First load supplemental_metadata.csv file.</p>

In [12]:
supplemental_df = pd.read_csv("/kaggle/input/asl-fingerspelling/supplemental_metadata.csv")

<p style="font-family: consolas; font-size: 16px;">⚪ Let's look how the data looks like.</p>

In [13]:
supplemental_df.head()

path   file_id  sequence_id  \
0  supplemental_landmarks/33432165.parquet  33432165   1535467051   
1  supplemental_landmarks/33432165.parquet  33432165   1535499058   
2  supplemental_landmarks/33432165.parquet  33432165   1535530550   
3  supplemental_landmarks/33432165.parquet  33432165   1535545499   
4  supplemental_landmarks/33432165.parquet  33432165   1535585216   

   participant_id                                    phrase  
0             251         coming up with killer sound bites  
1             239                we better investigate this  
2             245          interesting observation was made  
3              38              victims deserve more redress  
4             254  knee bone is connected to the thigh bone

<p style="font-family: consolas; font-size: 16px;">⚪ Show a discribe of the dataframe with its basic information.</p>

In [14]:
supplemental_df.describe()

file_id   sequence_id  participant_id
count  5.295800e+04  5.295800e+04    52958.000000
mean   9.680392e+08  1.072800e+09      132.738661
std    5.779288e+08  6.165748e+08       81.745528
min    3.343216e+07  2.869900e+04        0.000000
25%    4.717666e+08  5.411308e+08       53.000000
50%    8.972877e+08  1.069840e+09      135.000000
75%    1.471342e+09  1.606032e+09      216.000000
max    2.100074e+09  2.147473e+09      254.000000

<p style="font-family: consolas; font-size: 16px;">🔴 Let's try to visualize sequence <code>1535467051</code> from the file <code>33432165</code>.</p>

In [15]:
sequence_id = 1535467051
file_id = 33432165

In [16]:
path_to_sign = f"/kaggle/input/asl-fingerspelling/supplemental_landmarks/{file_id}.parquet"
sign = pd.read_parquet(path_to_sign)

<p style="font-family: consolas; font-size: 16px;">⚪ Here is what is inside this parquet file:</p>

In [17]:
sign

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1535467051       0  0.473406  0.471368  0.476484  0.467808  0.471630   
1535467051       1  0.471909  0.471652  0.476131  0.468071  0.472056   
1535467051       2  0.474033  0.471113  0.476054  0.467614  0.471442   
1535467051       3  0.475442  0.472270  0.476926  0.468922  0.472692   
1535467051       4  0.476560  0.471422  0.475697  0.467995  0.471922   
...            ...       ...       ...       ...       ...       ...   
1577584204     164  0.679449  0.685916  0.685659  0.681438  0.687666   
1577584204     165  0.678333  0.688899  0.686320  0.683686  0.691057   
1577584204     166  0.677319  0.686685  0.684960  0.682521  0.688893   
1577584204     167  0.676152  0.683227  0.682084  0.679447  0.685307   
1577584204     168  0.675521  0.682818  0.681529  0.678796  0.684881   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
1535467051   0.474802  0.484624  0.407028  0.488582  ...        -0.122543   
1535467051   0.475196  0.484882  0.406707  0.489017  ...        -0.122476   
1535467051   0.474595  0.484442  0.406840  0.488658  ...        -0.122838   
1535467051   0.475905  0.485815  0.407603  0.490161  ...        -0.130950   
1535467051   0.475109  0.484853  0.406288  0.489202  ...        -0.108376   
...               ...       ...       ...       ...  ...              ...   
1577584204   0.690719  0.698897  0.598792  0.704758  ...              NaN   
1577584204   0.693675  0.699893  0.596086  0.705406  ...              NaN   
1577584204   0.691966  0.699586  0.595295  0.705741  ...        -0.226176   
1577584204   0.688465  0.696569  0.595163  0.703009  ...        -0.240375   
1577584204   0.687961  0.695801  0.595828  0.701940  ...        -0.127333   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
1535467051         -0.141624        -0.063140        -0.106380   
1535467051         -0.141538        -0.063057        -0.100017   
1535467051         -0.140607        -0.065127        -0.100445   
1535467051         -0.152878        -0.068532        -0.109924   
1535467051         -0.129024        -0.050887        -0.087473   
...                      ...              ...              ...   
1577584204               NaN              NaN              NaN   
1577584204               NaN              NaN              NaN   
1577584204         -0.233720        -0.142825        -0.224614   
1577584204         -0.255004        -0.139600        -0.223864   
1577584204         -0.125795        -0.070456        -0.139119   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
1535467051         -0.130670        -0.144320        -0.074918   
1535467051         -0.126249        -0.140772        -0.080366   
1535467051         -0.123355        -0.135395        -0.081785   
1535467051         -0.140234        -0.159326        -0.081440   
1535467051         -0.115227        -0.132597        -0.059056   
...                      ...              ...              ...   
1577584204               NaN              NaN              NaN   
1577584204               NaN              NaN              NaN   
1577584204         -0.215298        -0.195754        -0.162544   
1577584204         -0.214905        -0.192707        -0.158705   
1577584204         -0.130074        -0.110871        -0.088630   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
1535467051         -0.114648        -0.136452        -0.149689  
1535467051         -0.115011        -0.134508        -0.144475  
1535467051         -0.113771        -0.129102        -0.135660  
1535467051         -0.121563   

<p style="font-family: consolas; font-size: 16px;">⚪ The number of unique sequences in an <code>.parquet</code> file is <b>1000</b>.</p>

In [18]:
len(np.unique(sign.index))

1000

<p style="font-family: consolas; font-size: 16px;">⚪ Let's get only sequence <code>1535467051</code> from the file.</p>

In [19]:
sequence = sign[sign.index == sequence_id]
sequence

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1535467051       0  0.473406  0.471368  0.476484  0.467808  0.471630   
1535467051       1  0.471909  0.471652  0.476131  0.468071  0.472056   
1535467051       2  0.474033  0.471113  0.476054  0.467614  0.471442   
1535467051       3  0.475442  0.472270  0.476926  0.468922  0.472692   
1535467051       4  0.476560  0.471422  0.475697  0.467995  0.471922   
...            ...       ...       ...       ...       ...       ...   
1535467051     142  0.481872  0.480452  0.484781  0.476917  0.480940   
1535467051     143  0.483839  0.479552  0.484142  0.476042  0.479986   
1535467051     144  0.485219  0.481192  0.485641  0.477435  0.481628   
1535467051     145  0.484826  0.481760  0.486053  0.477720  0.482159   
1535467051     146  0.484951  0.479347  0.483790  0.475579  0.479756   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
1535467051   0.474802  0.484624  0.407028  0.488582  ...        -0.122543   
1535467051   0.475196  0.484882  0.406707  0.489017  ...        -0.122476   
1535467051   0.474595  0.484442  0.406840  0.488658  ...        -0.122838   
1535467051   0.475905  0.485815  0.407603  0.490161  ...        -0.130950   
1535467051   0.475109  0.484853  0.406288  0.489202  ...        -0.108376   
...               ...       ...       ...       ...  ...              ...   
1535467051   0.484109  0.493737  0.415482  0.498035  ...              NaN   
1535467051   0.483198  0.492968  0.414613  0.497181  ...              NaN   
1535467051   0.484757  0.494281  0.414899  0.498482  ...              NaN   
1535467051   0.485115  0.494135  0.414605  0.498052  ...        -0.059908   
1535467051   0.482840  0.492235  0.413264  0.496277  ...        -0.026437   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
1535467051         -0.141624        -0.063140        -0.106380   
1535467051         -0.141538        -0.063057        -0.100017   
1535467051         -0.140607        -0.065127        -0.100445   
1535467051         -0.152878        -0.068532        -0.109924   
1535467051         -0.129024        -0.050887        -0.087473   
...                      ...              ...              ...   
1535467051               NaN              NaN              NaN   
1535467051               NaN              NaN              NaN   
1535467051               NaN              NaN              NaN   
1535467051         -0.051418        -0.029062        -0.072495   
1535467051         -0.022494        -0.007754        -0.035062   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
1535467051         -0.130670        -0.144320        -0.074918   
1535467051         -0.126249        -0.140772        -0.080366   
1535467051         -0.123355        -0.135395        -0.081785   
1535467051         -0.140234        -0.159326        -0.081440   
1535467051         -0.115227        -0.132597        -0.059056   
...                      ...              ...              ...   
1535467051               NaN              NaN              NaN   
1535467051               NaN              NaN              NaN   
1535467051               NaN              NaN              NaN   
1535467051         -0.059979        -0.040402        -0.044340   
1535467051         -0.026402        -0.013592        -0.016824   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
1535467051         -0.114648        -0.136452        -0.149689  
1535467051         -0.115011        -0.134508        -0.144475  
1535467051         -0.113771        -0.129102        -0.135660  
1535467051         -0.121563   

<p style="font-family: consolas; font-size: 16px;">🔴 Now we can visualize and sequence with the phrase.</p>

In [20]:
sequence_phrase = get_phrase(supplemental_df, file_id, sequence_id)
visualise2d_landmarks(sequence, f"Phrase: {sequence_phrase}")

In [ ]:
# (⁠ ⁠ꈍ⁠ᴗ⁠ꈍ⁠) WORK STILL IN PROGRESS

# <div style="box-shadow: rgba(240, 46, 170, 0.4) -5px 5px inset, rgba(240, 46, 170, 0.3) -10px 10px inset, rgba(240, 46, 170, 0.2) -15px 15px inset, rgba(240, 46, 170, 0.1) -20px 20px inset, rgba(240, 46, 170, 0.05) -25px 25px inset; padding:20px; font-size:30px; font-family: consolas; display:fill; border-radius:15px; color: rgba(240, 46, 170, 0.7)"> <b> ༼⁠ ⁠つ⁠ ⁠◕⁠‿⁠◕⁠ ⁠༽⁠つ Thank You!</b></div>

<p style="font-family:verdana; color:rgb(34, 34, 34); font-family: consolas; font-size: 16px;"> 💌 Thank you for taking the time to read through my notebook. I hope you found it interesting and informative. If you have any feedback or suggestions for improvement, please don't hesitate to let me know in the comments. <br><br> 🚀 If you liked this notebook, please consider upvoting it so that others can discover it too. Your support means a lot to me, and it helps to motivate me to create more content in the future. <br><br> ❤️ Once again, thank you for your support, and I hope to see you again soon!</p>